In [42]:
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM
import bitsandbytes as bnb
import pandas as pd
import numpy as np
from dotenv import load_dotenv
import os
import json
from utils_gen import to_csv, Rephraser

In [43]:
openai_api_key = os.getenv('OPENAI_API_KEY')
openai_model="gpt-4.1-nano"

In [44]:
from openai import OpenAI

class ChatGPTClient(Rephraser):
    def __init__(self, api_key, model_name):
        self.client = OpenAI()
        self.client.api_key = api_key
        self.model_name = model_name

    def gen(self, text_to_rephrase, query_task, temperature):
        query = self.compute_query(text_to_rephrase, query_task)
        
        response = self.client.responses.create(
            model= self.model_name,
            temperature= temperature,
            max_output_tokens=4192,
            input=[
                {
                    "role": "user",
                    "content": query
                }
            ],
        )
        return response.output_text

api_client = ChatGPTClient(openai_api_key, openai_model)

# data

In [45]:
chapters = pd.read_csv("../dataframe_2800-5600ch_marker_chapters_FINAL_CHATGPT.csv")
chapters = chapters.dropna()
# print a few random paragraphs from the dataframe paragraphs
# for i in range(5):
#     print(chapters.iloc[i]["sample"])
#     print("-" * 50)
#     print()

In [46]:
print(len(chapters))
chapters.head()

46675


original_index  document_id  \
0               1        10589   
1               3        10589   
2               5        10589   
3               7        10589   
4               9        10589   

                                              sample  \
0  Tema tezei de doctorat este de actualitate și ...   
1  Prin deșeuri industriale nerecuperabile se înț...   
2  Principalele surse de generare a țunderului pe...   
3  Cenușile piritice au rezultat de la fabricile ...   
4  Ținând seama de solicitările la care sunt supu...   

                                               title  
0  1.1 Descrierea esențializată a obiectului cerc...  
1  2.3 Reciclarea deșeurilor industriale nerecupe...  
2                                   3.2.1.6 Țunderul  
3          3.3.3 Cenuși piritice (industria chimică)  
4  4.2.3 Calitatea peletelor utilizate în încărcă...

# gen

In [ ]:
# queries = ["rephrase", "summarize", "continue"]
# temperature_max_change = 0.2

# for index in range(0, 3):
#     row = chapters.iloc[index]
#     original_index = row["original_index"]
#     chapter = row["sample"]

#     temperature = 1 + np.random.uniform(-temperature_max_change, temperature_max_change)
#     query_id = index % len(queries) 
#     query_task = queries[query_id]
    
        
#     generated = api_client.gen(chapter, query_task, temperature)
#     print(f"Original Index:\n {original_index}")
#     print(f"Original Chapter:\n {chapter}")
#     print(f"Query Task:\n {query_task}")
#     print(f"Temperature:\n {temperature}")
#     print(f"Generated Text:\n {generated}")
#     print("-" * 50)

Original Index: 1
Original Chapter: Tema tezei de doctorat este de actualitate și se referă la realizarea unor studii și cercetări privind reciclarea deșeurilor mărunte și pulverulente, pentru a putea fi folosite în încărcătura cuptoarelor cu arc electric la elaborarea oțelului.

Deșeurile feroase pulverulente și mărunte rezultate în diferite faze a proceselor industriale (în majoritatea cazurilor siderurgice), reprezintă o valoare intrinsecă, ce este determinată de conținutul de fier (fier legat chimic și metalic) care poate înlocui în mod corespunzător materia primă, respectiv minereul de fier sau fonta, în procesele siderurgice. Aceste deșeuri feroase pulverulente provin în cea mai mare parte din activitatea siderurgică și, în general, acestea rezultă din diferitele operații de epurare a gazelor evacuate și a apelor reziduale, fie sub formă uscată (din instalațiile de epurare uscată), fie sub formă de praf umed sau nămol (din instalațiile de epurare umede). Deșeurile feroase mărunte

In [47]:
start_index = 23000
end_index = 25000

In [48]:
# Creating an array of json tasks

# queries = ["rephrase", "summarize", "continue"]
queries = ["non_ai_doctorat", "non_ai_doctorat_summary", "non_ai_doctorat_continue"] # ["rephrase", "summarize", "continue"]
temperature_max_change = 0.2
tasks = []
ouput_arr = []

for index in range(start_index, end_index):
    row = chapters.iloc[index]
    original_index = row["original_index"]
    chapter = row["sample"]
    document_id = row["document_id"]
    title = row["title"]

    temperature = 1 + np.random.uniform(-temperature_max_change, temperature_max_change)
    query_id = index % len(queries)
    query_task = queries[query_id]

    task = {
        "custom_id": f"task-{original_index}",
        "method": "POST",
        "url": "/v1/responses",
        "body": {
            # This is what you would have in your Chat Completions API call
            "model": openai_model,
            "temperature": temperature,
            "max_output_tokens": 4192,
            "input": [
                {
                    "role": "user",
                    "content": api_client.compute_query(chapter, query_task),
                }
                ],
            },
        }
    tasks.append(task)
    
    ouput_arr.append({
        "original_index": original_index,
        "document_id": document_id,
        "title": title,
        "task": query_task,
        "chapter": chapter,
        "temperature": temperature,
    })

In [49]:
df_without_gen_filename= f'../CHATGPT_without_gen_{start_index}_{end_index}.csv'

In [50]:
output_df_without_gen = pd.DataFrame(ouput_arr)
output_df_without_gen.to_csv(df_without_gen_filename, index=False)

In [51]:
import json

print(json.dumps(tasks, indent=4, ensure_ascii=False))

[
    {
        "custom_id": "task-46001",
        "method": "POST",
        "url": "/v1/responses",
        "body": {
            "model": "gpt-4.1-nano",
            "temperature": 1.0703534375714698,
            "max_output_tokens": 4192,
            "input": [
                {
                    "role": "user",
                    "content": "Continuă textul următor, extras dintr-un subcapitol de teză doctorală, astfel încât să pară scris de un doctorand român și să nu poată fi identificat ca fiind generat de inteligență artificială:\nAcest model a fost construit ca instrument practic în sfera constructivismului social unde, se consideră că, oamenii își dezvoltă identitățile prin intermediul interacțiunilor sociale. Important de menționat în această încadrare teoretică (în vederea înțelegerii modelului și influenței ridicate a modelului medical) este că, perspectiva constructivismului social, atât în sociologie, cât și în psihologie, se află în opoziție cu abordarea pozitivistă, 

In [52]:
file_name = f'data/batch_tasks_{start_index}_{end_index}.jsonl'

In [53]:

with open(file_name, 'w') as file:
    for obj in tasks:
        file.write(json.dumps(obj, ensure_ascii=False) + '\n')

In [54]:
batch_file = api_client.client.files.create(
  file=open(file_name, "rb"),
  purpose="batch"
)

In [55]:
batch_job = api_client.client.batches.create(
  input_file_id=batch_file.id,
  endpoint="/v1/responses",
  completion_window="24h"
)

In [59]:
batch_job = api_client.client.batches.retrieve('batch_68387f28ba408190b5f2f3e73efe6877') #batch_68382fb155c48190af3cfa424ab6a38b
print(batch_job)

Batch(id='batch_68387f28ba408190b5f2f3e73efe6877', completion_window='24h', created_at=1748533032, endpoint='/v1/responses', input_file_id='file-1AqQNr2P4pm1y3oMdat19M', object='batch', status='completed', cancelled_at=None, cancelling_at=None, completed_at=1748533591, error_file_id=None, errors=None, expired_at=None, expires_at=1748619432, failed_at=None, finalizing_at=1748533460, in_progress_at=1748533034, metadata=None, output_file_id='file-Si3H5PknqX6iDbT8tqaSEC', request_counts=BatchRequestCounts(completed=2000, failed=0, total=2000))


In [65]:
result_file_id = batch_job.output_file_id
result = api_client.client.files.content(result_file_id).content

In [66]:
result_file_name = file_name.replace(".jsonl", "_result.jsonl")

with open(result_file_name, 'wb') as file:
    file.write(result)

In [67]:

results = []
with open(result_file_name, 'r', encoding='utf-8') as file:
    for line in file:
        # Parsing the JSON string into a dict and appending to the list of results
        json_object = json.loads(line.strip())
        results.append(json_object)

In [68]:
print(json.dumps(results[:10], indent=4, ensure_ascii=False))

[
    {
        "id": "batch_req_683880d59e0481909a6c2690450a960f",
        "custom_id": "task-46001",
        "response": {
            "status_code": 200,
            "request_id": "f1c63a30d660e1220223ef8861437cfa",
            "body": {
                "id": "resp_6838807bcc208191a5ceed7fc5afc1a801d9f1f1a444fcce",
                "object": "response",
                "created_at": 1748533371,
                "status": "completed",
                "background": false,
                "error": null,
                "incomplete_details": null,
                "instructions": null,
                "max_output_tokens": 4192,
                "model": "gpt-4.1-nano-2025-04-14",
                "output": [
                    {
                        "id": "msg_6838807c69988191b683af0688c850af01d9f1f1a444fcce",
                        "type": "message",
                        "status": "completed",
                        "content": [
                            {
                       

In [69]:
output_data = []
for result in results:
    custom_id = result.get("custom_id")
    original_index = None
    if custom_id:
        original_index = int(custom_id.split("-")[1])

    output_text = None
    response_body = result.get("response", {}).get("body", {})
    if response_body:
        output_list = response_body.get("output", [])
        if output_list:
            content_list = output_list[0].get("content", [])
            if content_list:
                output_text = content_list[0].get("text")

    # print (f"Original Index:\n {original_index}")
    # print (f"Output Text:\n {output_text}")
    if original_index is not None and output_text is not None:
        output_data.append(
            {
                "original_index": original_index,
                "generated": output_text,
            }
        )

# Create a pandas DataFrame from the collected data
output_df_gen = pd.DataFrame(output_data)

In [70]:
output_df_gen

original_index                                          generated
0              46001  În acest sens, se subliniază ideea că eliminar...
1              46003  Termenul de "cerințe educaționale speciale" (C...
2              46005  Educația specială, sau „instruirea special pro...
3              46007  - Dimensiunea socială, care include relațiile ...
4              46009  Viteza cu care sunt publicate, la nivel global...
...              ...                                                ...
1995           49991  Această selecție de citate evidențiază multipl...
1996           49993  Unul dintre sensurile oferite de dicționar pen...
1997           49995  Castingul, în Statele Unite, a evoluat de la o...
1998           49997  Această diferență fundamentală scoate în evide...
1999           49999  Fenomenul reprezentativ în istoria teatrului, ...

[2000 rows x 2 columns]

In [71]:
# join output_df and chapters on original_index

output_df_without_gen = pd.read_csv(df_without_gen_filename)
output_df = output_df_gen.merge(output_df_without_gen, on="original_index", how="left")

In [72]:
output_df_without_gen

original_index  document_id  \
0              46001        10247   
1              46003        10247   
2              46005        10247   
3              46007        10247   
4              46009        10247   
...              ...          ...   
1995           49991        11614   
1996           49993        13447   
1997           49995        13447   
1998           49997        13447   
1999           49999        13447   

                                                  title  \
0                       Modelul social al dizabilității   
1     I.1.3.1. Cerințe Educaționale Speciale și Educ...   
2                                     Educația specială   
3     I.1.3.3. Bariere în învățare și climat educați...   
4     I.1.4. Discuții și direcții de acțiune în cont...   
...                                                 ...   
1995          Caleidoscop: Muzica în cultura universală   
1996                                   Ipoteze de lucru   
1997          1.5. Industria de casting și "actoriiˮ ei   
1998           1.6. Admiterea la actorie versus casting   
1999                              2.2. Cartelul francez   

                          task  \
0     non_ai_doctorat_continue   
1              non_ai_doctorat   
2      non_ai_doctorat_summary   
3     non_ai_doctorat_continue   
4              non_ai_doctorat   
...                        ...   
1995  non_ai_doctorat_continue   
1996           non_ai_doctorat   
1997   non_ai_doctorat_summary   
1998  non_ai_doctorat_continue   
1999           non_ai_doctorat   

                                                chapter  temperature  
0     Acest model a fost construit ca instrument pra...     1.070353  
1     Sintagma cerințe educaționale speciale (CES) a...     0.964923  
2     Educație specială sau ,,instruirea special pro...     1.176321  
3     Modalităților riguroase de a identifica cadrel...     0.996440  
4     Viteza amețitoare cu care sunt publicate zeci ...     1.040132  
...                                                 ...          ...  
1995  "Muzica este o putere spirituală în stare să l...     0.951967  
1996  Cel de-al doilea sens furnizat de dicționar cu...     0.943024  
1997  Castingul, influențat de o serie de factori so...     0.846007  
1998  Considerațiile următoare se bazează pe studiil...     0.908355  
1999  Adevărat fenomen în istoria teatrului, Cartelu...     1.097304  

[2000 rows x 6 columns]

In [73]:
output_df.head()

original_index                                          generated  \
0           46001  În acest sens, se subliniază ideea că eliminar...   
1           46003  Termenul de "cerințe educaționale speciale" (C...   
2           46005  Educația specială, sau „instruirea special pro...   
3           46007  - Dimensiunea socială, care include relațiile ...   
4           46009  Viteza cu care sunt publicate, la nivel global...   

   document_id                                              title  \
0        10247                    Modelul social al dizabilității   
1        10247  I.1.3.1. Cerințe Educaționale Speciale și Educ...   
2        10247                                  Educația specială   
3        10247  I.1.3.3. Bariere în învățare și climat educați...   
4        10247  I.1.4. Discuții și direcții de acțiune în cont...   

                       task  \
0  non_ai_doctorat_continue   
1           non_ai_doctorat   
2   non_ai_doctorat_summary   
3  non_ai_doctorat_continue   
4           non_ai_doctorat   

                                             chapter  temperature  
0  Acest model a fost construit ca instrument pra...     1.070353  
1  Sintagma cerințe educaționale speciale (CES) a...     0.964923  
2  Educație specială sau ,,instruirea special pro...     1.176321  
3  Modalităților riguroase de a identifica cadrel...     0.996440  
4  Viteza amețitoare cu care sunt publicate zeci ...     1.040132

In [74]:
output_df = pd.DataFrame(output_df)
output_df.to_csv(f'../FINAL_CHATGPT_{start_index}_{end_index}.csv', index=False)